In [1]:
import pandas as pd
import matplotlib.pyplot as plt
from pandas.api.types import is_numeric_dtype
stack_dfs = pd.read_csv("StateGovFinances2005to2021.csv", index_col = ["State", "Year", "Format"], low_memory =False).sort_index()
panel_dfs_dict = {k:stack_dfs[stack_dfs.index.get_level_values(2)==k].reset_index().set_index(["State","Year"]).sort_index() for k in stack_dfs.index.get_level_values(2).unique()}
for key, df in panel_dfs_dict.items():
    for col in df.columns:
        if not is_numeric_dtype(df[col]):
            try:
                df[col] = pd.to_numeric(df[col], errors = "coerce")
                df[col] = df[col].fillna(0)
                df[col] = df[col].astype(int)
            except:
                pass
        else:
            df[col] = df[col].fillna("")



In [2]:

keys = ["GENERAL REVENUE","EXPENDITURE", 'INDIVIDUAL INCOME', 'CORPORATE INCOME', "PROPERTY", "SPECIAL ASSESSMENTS",
        "SALES AND GROSS RECEIPTS", "GENERAL SALES", "MOTOR FUEL", ]	
keys = ["1" + k for k in keys]
plot_df = panel_dfs_dict['State & local government amount']#[keys]
plot_df.rename(columns = {k:k.replace("1", "").title() for k in plot_df.keys()}, inplace = True)
plot_df["Total Income"] = plot_df["Individual Income"].add(plot_df["Corporate Income"])

pct_df = plot_df.apply(lambda x: x.div(plot_df["General Revenue"]) if is_numeric_dtype(x) else x)       

/tmp/ipykernel_31524/2035272073.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  plot_df["Total Income"] = plot_df["Individual Income"].add(plot_df["Corporate Income"])


In [3]:
# states = pct_df.index.get_level_values("State").unique()
# color_map = {value: idx for idx, value in enumerate(states)}
# pct_df['state'] = pct_df.index.get_level_values('State').map(color_map)
# ax = pct_df.plot.scatter(x = "Property", y = "Individual Income", c = "state", colorbar = False, cmap = "viridis", figsize = (20,10))
# # # Create a colorbar with the correct labels
# cbar = plt.colorbar(ax.collections[0], ticks=range(len(states)))
# cbar.ax.set_yticklabels(states)
# plt.show()

In [4]:
corr_df = pct_df.groupby("State")[["Property", "Total Income"]].corr()["Property"]
corr_df[corr_df.index.get_level_values(1)=="Total Income"].mean()

-0.24406087843548963

In [5]:
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
from plotly.subplots import make_subplots
from homebrewedFunctions.functions import *

In [7]:
create_scatter_dropdown(pct_df[list(pct_df.keys())[:50]], 
                        filename = "IncomePropertyAssessmentSalesFuelTaxesPctTotalRevenue.html", 
                        show_fig = True)



In [ ]:
pct_df.values